## Generate mppnp flux information

<b>Warning: I am making the assumption of constant rho and temperature profiles for the whole simulation in the turning it on for a couple cycles. If that isn't true you will have to do this for a variety of cycles.</b>


What we need to do this is the reaction rate information for all reactions in our network. To get that information from ```mppnp.f```, you need to make some edits to the existing code. 

#### Step 1: Locate where the subroutine ```printonecycle``` is defined in ```mppnp.f```

#### Step 2. Edit ```printonecycle```

This section inside ```printonecycle``` needs the additions in red to include the array of reaction rates ```v```
<pre>
<code>
       ! write out fluxes
        if ((iplot_flux_type.eq.0).or.(iplot_flux_type.eq.2)) then
          open(769,file='fluxes/flux_'//CMODELL//'_'//cprefix(1:
     $            5)//".DAT")
          write(769,*)'Model = ',MODELL,', Zone = ',zone,
     $          ', Age = ',dzeit
          write(769,'(3x,a,2x,4(a,2x),6x,4(a,2x),2x,a,2(4x,a))')'#',
     1   'Z_k1','A_k1','Z_k3','A_k3','Z_k5','A_k5','Z_k7','A_k7',
     2   'flux [dY/dt]','energy [erg/(g*s)]','timescale reac [s]'<span style="color:red;">, 'v'</span>
          do i=1,nrnc1
              write(769,'(i5,4(2x,i3),8x,4(2x,i3),3(8x,ES12.5))')i,
     1   int(znetw(k1(i))),int(anetw(k1(i))),
     2   int(znetw(k3(i))),int(anetw(k3(i))),
     3   int(znetw(k5(i))),int(anetw(k5(i))),
     4   int(znetw(k7(i))),int(anetw(k7(i))),
     5   max(1.0d-99,flux_to_print_0(i)),
! CR    6   max(1.0d-99,flux_to_print_0(i)*bind_energy_diff(i)),
     6   max(1.0d-99,flux_to_print_0(i))*bind_energy_diff(i),
     7   min(1.0d+90,time_scale_reac(i))<span style="color:red;">,</span>
     <span style="color:red;">8   v(i)</span>
          end do
          close(769)
        end if
</code>
</pre>

#### Step 3. Allow ```printonecycle``` to execute
Also in the main code you will find the call to ```printonecycle```. You will want to make the edits I suggest so that it will actually call it.
<pre>
<code>
               !CR: flux plot implementation
               !write out fluxes
               <span style="color:red;">call printonecycle(itag,icountmod,iolevel,dzeit,
     &#36     T9,rho,y0,ZIS,considerisotope ,AN ,ZN,
     &#36     isomeric_state,iplot_flux_option,v,
     &#36     considerreaction,
     &#36     reaction_rev_len,reaction_rev_num,reaction_rev_j,
     &#36       iplot_flux_type,xm(itag),ipid)</span>
                if (iplot_flux_option.gt.0) then
                ! every icountmodw,iplot_flux_tinterval cycles
                if (modulo(icountmodw,iplot_flux_tinterval).eq.0) then
                ! every iplot_flux_sinterval cycles
                if (modulo(itag,iplot_flux_sinterval).eq.0) then
                !write(*,*) 'print fluxfile, cycle: ',icountmodw,', zone: ',itag
                call printonecycle(itag,icountmod,iolevel,dzeit,
     $     T9,rho,y0,ZIS,considerisotope ,AN ,ZN,
     $     isomeric_state,iplot_flux_option,v,
     $     considerreaction,
     $     reaction_rev_len,reaction_rev_num,reaction_rev_j,
     $       iplot_flux_type,xm(itag),ipid)
                !write(*,*) 'finished printonecycle'
                end if
                end if
                end if
                !CR
</code>
</pre>

#### Step 4. Get ready to run
Recompile ```mppnp.f```, create a directory called ```fluxes``` in the same directory as where you are running, and run with the ```ppn_frame.input``` parameter ```modstop  = 2```. This will generate the flux files which you can then do what you want with them.

<i>Make sure that you undo these changes afterwards or have a separate version of ```mppnp.f``` with these edits. The flux files that are generated can be quite overbearing in terms of file size.</i>

## Ensure that the fluxes information is ```pandas``` friendly

Since the way the mppnp flux plots are generated requires ```pandas```, it is important that you do this step since ```printonecycle``` doesn't format the files correctly (and I am unsure why at this moment). This step will basically just fix it so that the columns are good to go.

#### Step 1. Create ```fluxes_fixed```

In the same directory as your folder ```fluxes``` create another folder called ```fluxes_fixed```. This is where the fixed flux information from ```mppnp``` will be saved

#### Step 2. Run the cells below

Since this is parallelized, it will only take a handful of seconds.

In [1]:
import os
from pathlib import Path
from multiprocessing import Pool
from functools import partial

In [2]:
def process_single_file(file, fixed_dir):
    HEADER = '#\tZ_k1\tA_k1\tZ_k3\tA_k3\tZ_k5\tA_k5\tZ_k7\tA_k7\tflux [dY/dt]\tenergy [erg/(g*s)]\ttimescale reac [s]'
    
    with open(file, mode='r') as f:
        lines = f.readlines()
    
    fixed = [lines[0]]  # Keep first line unchanged
    con = ''
    
    for i, line in enumerate(lines):
        if i == 0:
            continue
            
        splits = [piece for piece in line.split(' ') if piece != '']
        
        if i == 1:
            edit_line = HEADER
        else:
            if len(splits) > 1:
                edit_line = '\t'.join(splits)
            else:
                edit_line = splits[0]
        
        if i % 2 == 1:
            con = edit_line
        elif i % 2 == 0:
            if i == 2:
                con = con + '\t' + str(edit_line)
            else:
                con = con[:-2] + '\t' + str(edit_line)
            fixed.append(con)
            con = ''
    
    output_path = os.path.join(fixed_dir, os.path.basename(file))
    with open(output_path, mode='w') as f:
        f.writelines(fixed)

def process_flux_files(flux_dir, fixed_dir, n_processes=None):
    # Create output directory if it doesn't exist
    os.makedirs(fixed_dir, exist_ok=True)
    
    # Get list of files to process
    files = [os.path.join(flux_dir, f) for f in sorted(os.listdir(flux_dir)) 
             if not os.path.isdir(os.path.join(flux_dir, f))]
    
    # Create a partial function with fixed_dir
    process_func = partial(process_single_file, fixed_dir=fixed_dir)
    
    # Use all available CPU cores if n_processes is None
    with Pool(processes=n_processes) as pool:
        # Process files in parallel
        pool.map(process_func, files)

In [3]:
flux_dir = '/scratch/f/fherwig/jissa/OC_RUNS/MLT_RUNS/flux_run/fluxes'
fixed_dir = '/scratch/f/fherwig/jissa/OC_RUNS/MLT_RUNS/flux_run/fluxes_fixed'

process_flux_files(flux_dir, fixed_dir)